In [810]:
import pandas as pd
import panel as pn
import plotly.express as px
from plotly.graph_objects import Figure, Scatter, Bar, Choropleth
from plotly.subplots import make_subplots
import numpy as np

In [811]:
pn.extension("plotly")

In [812]:
df = pd.read_csv('./data/eduwa.csv')
df.head()

Unnamed: 0  NCES.School.ID State.School.ID  NCES.District.ID  \
0           1    530486002475   WA-31025-1656           5304860   
1           2    530270001270   WA-06114-1646           5302700   
2           3    530910002602   WA-34033-4500           5309100   
3           4    530003000001   WA-14005-2834           5300030   
4           5    530825002361   WA-32081-1533           5308250   

  State.District.ID Low.Grade High.Grade                       School.Name  \
0          WA-31025         6          8                10th Street School   
1          WA-06114        KG         12               49th Street Academy   
2          WA-34033         9         12  A G West Black Hills High School   
3          WA-14005        PK          6               A J West Elementary   
4          WA-32081         9         12   A-3 Multiagency Adolescent Prog   

                            District        County  ...          Phone  \
0         Marysville School District     Snohomish  ...  (360)965-0400   
1  Evergreen School District (Clark)         Clark  ...  (360)604-6700   
2           Tumwater School District      Thurston  ...  (360)709-7800   
3           Aberdeen School District  Grays Harbor  ...  (360)538-2131   
4            Spokane School District       Spokane  ...  (509)354-6299   

  Locale.Code LocaleType        LocaleSub  Charter Title.I.School  \
0        22.0     Suburb  Suburb: Midsize       No            Yes   
1        12.0       City    City: Midsize       No             No   
2        13.0       City      City: Small       No             No   
3        33.0       Town     Town: Remote       No            Yes   
4        12.0       City    City: Midsize       No             No   

   Title.1.School.Wide Student.Teacher.Ratio Free.Lunch Reduced.Lunch  
0                  Yes                  23.4       28.0           3.0  
1                  NaN                   8.4       53.0           9.0  
2                  NaN                  21.5      169.0          40.0  
3                  Yes                  15.9      292.0          10.0  
4                  NaN                   6.5       12.0           4.0  

[5 rows x 25 columns]

In [813]:
newdf = df[["County","Reduced.Lunch"]]
reducedLunchCounty = newdf.groupby(['County']).sum().sort_values(by="Reduced.Lunch",ascending=False).reset_index()
reducedLunchCounty['Cumulative'] = 100 * (reducedLunchCounty["Reduced.Lunch"].cumsum()/reducedLunchCounty["Reduced.Lunch"].sum())
reducedLunchCounty

County  Reduced.Lunch  Cumulative
0           King        16048.0   20.842912
1         Pierce        11210.0   35.402299
2      Snohomish         8087.0   45.905578
3          Clark         6388.0   54.202221
4        Spokane         5889.0   61.850770
5       Thurston         3162.0   65.957530
6         Kitsap         2998.0   69.851289
7         Benton         2412.0   72.983960
8        Whatcom         2003.0   75.585428
9         Yakima         1613.0   77.680369
10      Franklin         1592.0   79.748036
11         Grant         1551.0   81.762452
12        Skagit         1518.0   83.734009
13       Cowlitz         1201.0   85.293850
14       Clallam         1096.0   86.717319
15        Chelan         1046.0   88.075849
16        Island          952.0   89.312293
17      Okanogan          934.0   90.525359
18   Walla Walla          840.0   91.616339
19         Lewis          705.0   92.531983
20       Stevens          658.0   93.386584
21         Mason          642.0   94.220404
22         Adams          634.0   95.043834
23       Douglas          599.0   95.821807
24  Grays Harbor          510.0   96.484187
25       Whitman          382.0   96.980323
26      Kittitas          372.0   97.463472
27        Asotin          329.0   97.890772
28     Klickitat          264.0   98.233652
29     Jefferson          263.0   98.575232
30       Pacific          232.0   98.876550
31       Lincoln          205.0   99.142801
32      San Juan          193.0   99.393467
33         Ferry          120.0   99.549321
34  Pend Oreille          117.0   99.701279
35      Skamania          111.0   99.845445
36      Columbia           53.0   99.914280
37      Garfield           42.0   99.968829
38     Wahkiakum           24.0  100.000000

In [814]:
def graph_pareto(dataframe, col):
    df = dataframe.copy()

    data = [
        Bar(
          name = "Count",  
          x = df.County,
          y = df[f'{col}'], 
          marker= {"color": list(np.repeat('rgb(71, 71, 135)', 5)) + list(np.repeat('rgb(112, 111, 211)', len(df.index) - 5))}
        ),
        Scatter(
          line= {
            "color": "rgb(192, 57, 43)", 
            "width": 3
          }, 
          name = "Percentage", 
          x = df.County,
          y = df['Cumulative'], 
          yaxis= "y2",
          mode='lines+markers'
        ),
    ]

    layout = {
      # Title Graph
      "title": {
        'text': "Reduced Lunch by County<br><span style='font-size:15px; color: rgb(100, 100, 100);'>Reduced Lunch Individuals in Schools in Washington State</span>",
        'font': dict(size=30),
      },
      
      # Source/Caption
      "annotations": [{
        'xref': 'paper',
        'yref': 'paper',
        'x': 1, 
        'y': -0.5,
        'showarrow': False,
        'text': '<span style="font-size:12px; color: gray; font-family: Courier New, monospace;">Source: National Center for Education Statistics</span>',
        'align': 'right'
      }],
      
      # Font 
      "font": {
        "size": 14, 
        "color": "rgb(44, 44, 84)", 
        "family": "Times New Roman, monospace"
      },

      # Graph Box 
      "margin": {
        "b": 120, 
        "l": 50, 
        "r": 50, 
        "t": 100,
      }, 
      "height": 400, 

      # Graph Box 
      "plot_bgcolor": "rgb(255, 255, 255)", 


      # Settings Legend
      "legend": {
        "x": 0.79, 
        "y": 1.2, 
        "font": {
          "size": 12, 
          "color": "rgb(44, 44, 84)", 
          "family": "Courier New, monospace"
        },
        'orientation': 'h',
      },
      # Xaxis
      "xaxis": {
        "showline": True,
        "linecolor": "rgb(0, 0, 0)",
        "linewidth": 2,
        "ticks": "outside",
        "tickwidth": 2, 
        "tickcolor": 'rgb(0, 0, 0)',
        "range": [(-1),len(reducedLunchCounty.index)]
      },
      # Yaxis 1 position left

      "yaxis": {
        "title": "Count Reduced Lunch",
        "titlefont": {
        "size": 16,
        "color": "rgb(71, 71, 135)", 
        "family": "Courier New, monospace"
        },
        "showline": True,
        "linecolor": "rgb(0, 0, 0)",
        "linewidth": 2,
        "ticks": "outside",
        "tickwidth": 2, 
        "tickcolor": 'rgb(0, 0, 0)',
        #"automargin": True
        #"shift": -1
      }, 


      # Yaxis 2 position right
      "yaxis2": {
        "side": "right",
        "range": [0, 100], 
        "title": "Percentage of Total Reduced Lunch",
        "titlefont": {
          "size": 16, 
          "color": "rgb(71, 71, 135)", 
          "family": "Courier New, monospace"
        },
        "showline": True,
        "linecolor": "rgb(0, 0, 0)",
        "linewidth": 2,
        "overlaying": "y",
        "ticksuffix": " %",
        "ticks": "outside",
        "tickwidth": 2, 
        "tickcolor": 'rgb(0, 0, 0)',
        #"automargin": True
        #"shift": 1
      }, 
    }

    # Build Graph
    fig = Figure(data=data, layout=layout)
    fig.update_layout(autosize=True)
    # Show Graph
    fig.show()
    
    
    plotPane = pn.pane.Plotly(fig)
    source_annotation = pn.pane.Markdown(
        '<span style="font-size: 12px; color: gray;">Source: National Center for Education Statistics</span>',
        width=600, height=40, align="start"
    )

    # Combine Plotly graph and source annotation in a layout
    layout = pn.Column(plotPane, pn.Spacer(height=10),source_annotation, styles={"border": "1px solid black"})

    return layout
lunchfig = graph_pareto(reducedLunchCounty, 'Reduced.Lunch')

In [815]:
dfarrests = pd.read_excel('./data/MSP DFS Arrests 19-20Q1.xlsx', sheet_name='MSP DFS Arrests')
dfcodes = pd.read_excel('./data/MSP DFS Arrests 19-20Q1.xlsx', sheet_name='Codes', usecols="A:B", skiprows=74)

In [816]:
dfarrests = dfarrests[['Arrest Type','Age']].dropna()
dfarrests.head()

Arrest Type   Age
0           W  25.0
1           M  26.0
2           M  28.0
3           M  28.0
4           M  28.0

In [817]:
dfcodes.columns = ['Arrest Type', 'Long Form']
dfcodes.head()

Arrest Type    Long Form
0           F       Felony
1           J     Juvenile
2           M  Misdemeanor
3           W      Warrant
4           O        Other

In [818]:
mergeddf = dfarrests.merge(dfcodes, on='Arrest Type', how='inner')
mergeddf.head()

Arrest Type   Age    Long Form
0           W  25.0      Warrant
1           M  26.0  Misdemeanor
2           M  28.0  Misdemeanor
3           M  28.0  Misdemeanor
4           M  28.0  Misdemeanor

In [819]:
figviol = px.violin(
    mergeddf,
    x = "Age",
    y = "Long Form",
    box = True,
    points="all",
    color = "Long Form",
    range_x = [0, None],
    labels = {
        "Long Form" : "Arrest Type",
        "Age" : "Arrestee Age (Years)"
    },
    title = "Felony Arrests are Younger than other Arrests in Massachusetts<br><span style='font-size:12px; color: rgb(100, 100, 100);'>Age Distribution of Arrests in Massachusetts from January 2019 to March 2020 </span>"
)
figviol.update_layout(
    showlegend=False
)
figviol.show()

In [820]:
import json
def load_json(file):
    with open(file) as f:
        data = json.load(f)
        return data

In [821]:
bostondf = pd.read_excel('./data/BostonContrib.xlsx', dtype={"Zip": str})
bostonjson = load_json('./data/zip_codes.json')

bostondf = bostondf.dropna(subset=['Zip', 'Tender Type Description','Amount'])
bostondf.head()

Date         Contributor                     Address  \
0  1/2/2024    Bradley, Garrett        234 Causeway St #709   
1  1/2/2024  Eisenstadt, Joseph     2 Center Plaza Ste. 620   
2  1/2/2024       Faustin, Kurt     126 Border St. Unit 515   
3  1/2/2024     Lynch, Patricia           18 Tremont Street   
4  1/2/2024      Miller, Thomas  28 State Street, Suite 802   

                                  Addressfull    City State    Zip Occupation  \
0        234 Causeway St #709 Boston MA 02108  Boston    MA  02108   attorney   
1     2 Center Plaza Ste. 620 Boston MA 02108  Boston    MA  02108   Attorney   
2     126 Border St. Unit 515 Boston MA 02108  Boston    MA  02108    Founder   
3           18 Tremont Street Boston MA 02108  Boston    MA  02108   Attorney   
4  28 State Street, Suite 802 Boston MA 02108  Boston    MA  02108   ATTORNEY   

   Amount            Recipient Tender Type Description  
0  1000.0          Dolan, Mara             Credit Card  
1   500.0  Ryan, Marian Teresa                   Check  
2   100.0       Worrell, Brian             Credit Card  
3   200.0  Decker, Marjorie C.             Credit Card  
4   200.0           Lawn, John                   Check

In [822]:
bostondf['Tender Type Description'].value_counts()

Tender Type Description
Credit Card      10667
Check             7171
Transfer          5067
Not Specified      539
Other              307
Cash               127
Money Order         19
Name: count, dtype: int64

In [823]:
bostondfFiltered = bostondf.loc[bostondf['Tender Type Description'].isin(['Check','Credit Card'])]
bostondfFiltered.head()

Date         Contributor                     Address  \
0  1/2/2024    Bradley, Garrett        234 Causeway St #709   
1  1/2/2024  Eisenstadt, Joseph     2 Center Plaza Ste. 620   
2  1/2/2024       Faustin, Kurt     126 Border St. Unit 515   
3  1/2/2024     Lynch, Patricia           18 Tremont Street   
4  1/2/2024      Miller, Thomas  28 State Street, Suite 802   

                                  Addressfull    City State    Zip Occupation  \
0        234 Causeway St #709 Boston MA 02108  Boston    MA  02108   attorney   
1     2 Center Plaza Ste. 620 Boston MA 02108  Boston    MA  02108   Attorney   
2     126 Border St. Unit 515 Boston MA 02108  Boston    MA  02108    Founder   
3           18 Tremont Street Boston MA 02108  Boston    MA  02108   Attorney   
4  28 State Street, Suite 802 Boston MA 02108  Boston    MA  02108   ATTORNEY   

   Amount            Recipient Tender Type Description  
0  1000.0          Dolan, Mara             Credit Card  
1   500.0  Ryan, Marian Teresa                   Check  
2   100.0       Worrell, Brian             Credit Card  
3   200.0  Decker, Marjorie C.             Credit Card  
4   200.0           Lawn, John                   Check

In [824]:
print(set(bostondfFiltered['Zip'].values))

{'02118', '02129', '02126', '02131', '02116', '02113', '02124', '02108', '02122', '02111', '02115', '02110', '02134', '02199', '02210', '02119', '02130', '02136', '02135', '02109', '02125', '02114', '02127', '02121', '02215', '02132', '02120', '02128'}


In [825]:
bostonPiv = bostondfFiltered.pivot_table(index='Zip', columns='Tender Type Description', values='Amount', aggfunc="sum").astype('int')
bostonPiv['Highest'] = bostonPiv.idxmax(axis=1)
bostonPiv.columns.name = None
bostonPiv.index.name = None
bostonPiv = bostonPiv.rename_axis('Zip').reset_index()
bostonPiv['Zip'] = bostonPiv['Zip'].astype(str)
bostonPiv.head()

Zip   Check  Credit Card      Highest
0  02108  266417       253731        Check
1  02109   77354        91764  Credit Card
2  02110  147129        87701        Check
3  02111   75100        52470        Check
4  02113   46652        37838        Check

In [826]:
print(bostonjson['features'][0]['properties'])

{'OBJECTID': 1, 'ZIP5': '02134', 'Shape_Length': 0.1331438206588804, 'Shape_Area': 0.0003778714301533854, 'shape_wkt': None}


In [827]:
figchoro = px.choropleth(
    bostonPiv,
    geojson= bostonjson,
    locations='Zip',
    featureidkey='properties.ZIP5',
    hover_data='Check',
    color='Check',
    color_continuous_scale="Viridis",
    title="Check Contributions"
)

figchoro.update_geos(
    projection_type="mercator",
    fitbounds="locations"
)

figchoro.update_layout(
    coloraxis_colorbar_title="Contributions (USD)",
    margin={"l":1, "r":1}
    
)

figchoro2 = px.choropleth(
    bostonPiv,
    geojson= bostonjson,
    locations='Zip',
    featureidkey='properties.ZIP5',
    hover_data='Credit Card',
    color='Credit Card',
    color_continuous_scale="Viridis",
    title="Credit Card Contributions"
)

figchoro2.update_geos(
    projection_type="mercator",
    fitbounds="locations"
)

figchoro2.update_layout(
    coloraxis_colorbar_title="Contributions (USD)",
    margin={"l":1, "r":1}
)

figchoro.show()
figchoro2.show()

In [828]:
campaignSourceAnnotation = pn.pane.Markdown(
        '<span style="font-size: 12px; color: gray;">Source: Massachusetts Office of Campaign and Political Finance</span>',
        width=600, height=40, align="start"
    )

In [829]:
chorosComb = pn.Row(figchoro, figchoro2, sizing_mode="stretch_both", align="center")

chorotitle = pn.pane.Markdown(
        '<span style="font-size: 24px; color: black;">Campaign Contribution Amounts Vary Greatly by Tender Type and Location in Boston</span>',
        width=1000, height=40, align="center"
    )
chorosubtitle = pn.pane.Markdown(
        '<span style="font-size: 12px; color: gray;">Campaign Contributions by Zipcode in Boston Massachusetts</span>',
        width=600, height=40, align="center"
    )
chorosFull = pn.Column(chorotitle,chorosubtitle,chorosComb,campaignSourceAnnotation, styles={"border": "1px solid black"}, sizing_mode="stretch_height")


In [830]:
arrestSourceAnnotation = pn.pane.Markdown(
        '<span style="font-size: 12px; color: gray;">Source: Massachusetts Executive Office of Public Safety and Security</span>',
        width=600, height=40, align="start"
    )
arrestsfig = pn.Column(figviol, pn.VSpacer(), arrestSourceAnnotation, styles={"border": "1px solid black"}, sizing_mode="stretch_height")

In [831]:
dashbottom = pn.Row(chorosFull,arrestsfig, sizing_mode="stretch_height", styles={"border": "1px solid black"})
dash = pn.Column(lunchfig,dashbottom,sizing_mode="stretch_width")

In [832]:
#server = dash.show()

In [833]:
from bokeh.resources import INLINE
from pathlib import Path

dash.save(f"{Path.home()}/Documents/School/690V/index.html", resources=INLINE, embed=True)